In [1]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from sklearn.linear_model import LinearRegression
from joblib import Parallel, delayed
import httpx
import aiohttp
import asyncio
import time

In [2]:
pd.options.mode.chained_assignment = None

### EDA

In [3]:
# Загрузка датасета
df = pd.read_csv('temperature_data.csv', parse_dates=['timestamp'])
df.head()

city  timestamp  temperature  season
0  New York 2010-01-01    -1.670631  winter
1  New York 2010-01-02    -0.990672  winter
2  New York 2010-01-03     3.556789  winter
3  New York 2010-01-04    -1.721118  winter
4  New York 2010-01-05    -4.411674  winter

In [4]:
# Проверка типов данных
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 54750 entries, 0 to 54749
Data columns (total 4 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   city         54750 non-null  object        
 1   timestamp    54750 non-null  datetime64[ns]
 2   temperature  54750 non-null  float64       
 3   season       54750 non-null  object        
dtypes: datetime64[ns](1), float64(1), object(2)
memory usage: 1.7+ MB


In [5]:
# Описательные статистики
df.describe(include='all')

city            timestamp   temperature  season
count      54750                54750  54750.000000   54750
unique        15                  NaN           NaN       4
top     New York                  NaN           NaN  spring
freq        3650                  NaN           NaN   13800
mean         NaN  2014-12-30 12:00:00     18.288415     NaN
min          NaN  2010-01-01 00:00:00    -26.042894     NaN
25%          NaN  2012-07-01 00:00:00     11.206228     NaN
50%          NaN  2014-12-30 12:00:00     18.780396     NaN
75%          NaN  2017-06-30 00:00:00     26.086149     NaN
max          NaN  2019-12-29 00:00:00     55.060193     NaN
std          NaN                  NaN     10.979842     NaN

In [6]:
# Вычисление скользящего среднего с окном в 30 дней
grouped_df = df.groupby(['city'])

for city, group in grouped_df:
    df.loc[group.index, 'rolling_mean'] = group['temperature'].rolling(window=30).mean()
    df.loc[group.index, 'rolling_std'] = group['temperature'].rolling(window=30).std()

df = df.dropna()
df

city  timestamp  temperature  season  rolling_mean  rolling_std
29        New York 2010-01-30     9.245857  winter      0.112613     4.896877
30        New York 2010-01-31     2.895913  winter      0.264831     4.910490
31        New York 2010-02-01    -6.525404  winter      0.080340     5.060954
32        New York 2010-02-02    -0.543022  winter     -0.056320     5.019023
33        New York 2010-02-03    -1.781314  winter     -0.058327     5.019723
...            ...        ...          ...     ...           ...          ...
54745  Mexico City 2019-12-25     8.174663  winter     12.189621     5.383108
54746  Mexico City 2019-12-26     9.240142  winter     11.749971     5.045996
54747  Mexico City 2019-12-27     6.633155  winter     11.568562     5.131004
54748  Mexico City 2019-12-28    16.448924  winter     11.530699     5.089098
54749  Mexico City 2019-12-29    13.803313  winter     11.013962     3.860866

[54315 rows x 6 columns]

In [7]:
# Построим график средней температуры по скользящему среднему для всех городов
fig = px.line(df, x='timestamp', y='rolling_mean', color='city', title='Rolling mean temperature by cities')
fig.update_xaxes(title='date')
fig.update_yaxes(title='Rolling mean temperature (degrees c)')
fig.show()

In [8]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=df[df['city']=='Moscow']['timestamp'], y=df[df['city']=='Moscow']['temperature'], 
                         name='temperature', line=dict(color='CornflowerBlue', width=1)))
fig.add_trace(go.Scatter(x=df[df['city']=='Moscow']['timestamp'], y=df[df['city']=='Moscow']['rolling_mean'], 
                         name='temperature rolling mean', line=dict(color='Navy', width=4)))
fig.update_layout(title='Temperature and rolling mean temperature in Moscow', 
                  xaxis=dict(title=dict(text='date')),  yaxis=dict(title=dict(text='Temperature (degrees C)')))
fig.show()

In [9]:
# Получение линии тренда для одного города при помощи линейной регрессии
X = df[df['city']=='Mexico City'].dropna()[['timestamp']].astype('int')
y = df[df['city']=='Mexico City'].dropna()['rolling_mean']
reg = LinearRegression()
reg.fit(X, y)
pred = reg.predict(X)

In [10]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=df[df['city']=='Mexico City']['timestamp'], y=df[df['city']=='Mexico City']['temperature'], 
                         name='temperature', line=dict(color='CornflowerBlue', width=1)))
fig.add_trace(go.Scatter(x=df[df['city']=='Mexico City']['timestamp'], y=df[df['city']=='Mexico City']['rolling_mean'], 
                         name='temperature rolling mean', line=dict(color='Navy', width=4)))
fig.add_trace(go.Scatter(x=df[df['city']=='Mexico City']['timestamp'], y=pred, 
                         name='trend line', line=dict(color='Crimson', width=4)))
fig.update_layout(title='Temperature and rolling mean temperature in Mexico City', 
                  xaxis=dict(title=dict(text='date')),  yaxis=dict(title=dict(text='Temperature (degrees C)')))

In [11]:
# Определим направление линии тренда

trend_line_coef = reg.coef_[0]
if trend_line_coef > 0:
    print(f'Тренд восходящий с коэффициентом {trend_line_coef}')
elif trend_line_coef < 0:
    print(f'Тренд нисходящий с коэффициентом {trend_line_coef}')
else:
    print('Тренд без изменений (горизонтальная линия)')

Тренд нисходящий с коэффициентом -4.283020304305708e-19


In [12]:
# Температурные профили сезонов по городам
seasons_profile = df[['city', 'season', 'temperature']].groupby(['city', 'season'], as_index=False)\
                    .agg(temp_mean=('temperature', 'mean'), temp_std=('temperature', 'std'), 
                         temp_min=('temperature', 'min'), temp_max=('temperature', 'max'))
seasons_profile


city  season  temp_mean  temp_std   temp_min   temp_max
0          Beijing  autumn  16.206013  5.105279  -1.319941  31.689190
1          Beijing  spring  13.532876  4.938591  -4.964510  27.700372
2          Beijing  summer  26.670668  5.019855   9.305620  42.657388
3          Beijing  winter  -2.159349  5.017286 -16.545212  14.184590
4           Berlin  autumn  11.030841  4.939311  -6.843221  25.869659
5           Berlin  spring  10.011535  4.958291  -4.443505  26.031544
6           Berlin  summer  19.936992  5.085671   3.746157  35.077247
7           Berlin  winter   0.303250  4.942319 -15.486114  15.106645
8            Cairo  autumn  24.764598  4.948879   9.542805  40.019840
9            Cairo  spring  24.925759  5.152070   9.465858  40.579256
10           Cairo  summer  34.812124  5.112885  19.958788  51.970598
11           Cairo  winter  15.037695  4.817574  -3.774874  33.442909
12           Dubai  autumn  29.855511  5.059074  12.995345  46.251212
13           Dubai  spring  30.075094  4.943375  16.181465  45.057215
14           Dubai  summer  39.852631  4.928059  24.585486  55.060193
15           Dubai  winter  19.998825  4.939711   3.341856  37.762329
16          London  autumn  11.943428  4.972250  -5.961899  28.855569
17          London  spring  10.844394  5.006696  -5.360330  26.166769
18          London  summer  18.386386  4.907589   5.538006  35.095612
19          London  winter   5.136259  5.057364 -11.701662  20.796469
20     Los Angeles  autumn  19.871900  5.175254   4.868967  35.706170
21     Los Angeles  spring  18.299436  4.924526   0.096748  31.983673
22     Los Angeles  summer  25.000415  4.943080   7.912284  43.365931
23     Los Angeles  winter  14.938904  5.065325   0.741673  32.250795
24     Mexico City  autumn  14.949311  5.237501   1.189734  32.341076
25     Mexico City  spring  18.377955  4.918074   2.501672  33.516391
26     Mexico City  summer  20.007242  4.959934   6.267785  37.119959
27     Mexico City  winter  12.133638  5.091363  -4.307543  30.383189
28          Moscow  autumn   8.023404  4.904034  -6.300662  23.637882
29          Moscow  spring   5.088380  4.870299 -11.977895  20.037911
30          Moscow  summer  18.032592  5.033734   2.281386  32.590492
31          Moscow  winter -10.136712  4.885720 -26.042894   4.752044
32          Mumbai  autumn  29.870599  4.784817  16.444048  45.630445
33          Mumbai  spring  30.168352  5.077500  13.112208  45.990546
34          Mumbai  summer  34.681881  5.032299  19.201062  51.889113
35          Mumbai  winter  24.922312  5.262683   9.863008  42.880837
36        New York  autumn  14.665017  5.040677   1.409721  29.744003
37        New York  spring   9.900180  4.989939  -5.698364  27.008551
38        New York  summer  24.920255  4.847927   7.741834  44.786657
39        New York  winter   0.052858  4.998612 -15.692108  15.061622
40           Paris  autumn  12.912253  5.039887  -2.416250  27.166641
41           Paris  spring  11.826818  4.834465  -4.226405  31.796900
42           Paris  summer  19.912864  4.920801   4.666086  39.627739
43           Paris  winter   3.778075  5.000884 -10.308451  20.963936
44  Rio de Janeiro  autumn  24.876437  4.933885   5.191561  42.778048
45  Rio de Janeiro  spring  25.501076  5.138639  10.580949  42.177007
46  Rio de Janeiro  summer  30.127432  5.143918  11.870232  45.295363
47  Rio de Janeiro  winter  20.116951  5.061819   4.055122  35.933484
48       Singapore  autumn  27.045316  4.913545  10.952830  40.534392
49       Singapore  spring  27.881475  5.081678  10.376565  43.441785
50       Singapore  summer  27.723291  4.913116  11.837866  45.501343
51       Singapore  winter  26.955510  4.990689   8.482920  43.800337
52          Sydney  autumn  19.836169  4.892517   5.376055  35.476170
53          Sydney  spring  17.911823  4.870772   3.093182  33.544323
54          Sydney  summer  25.054763  5.161889   9.066674  43.865638
55          Sydney  winter  12.295201  4.957363  -5.988891  26.075233
56           Tokyo  autu

In [13]:
# Поиск аномальных значений температуры относительно средней температуры для сезона по городам
df = pd.merge(df, seasons_profile, how='inner', on=['city', 'season'])
df['anomaly'] = abs(df['temperature']) > abs(df['temp_mean']) + df['temp_std'] * 2
df.head(30)

city  timestamp  temperature  season  rolling_mean  rolling_std  \
0   New York 2010-01-30     9.245857  winter      0.112613     4.896877   
1   New York 2010-01-31     2.895913  winter      0.264831     4.910490   
2   New York 2010-02-01    -6.525404  winter      0.080340     5.060954   
3   New York 2010-02-02    -0.543022  winter     -0.056320     5.019023   
4   New York 2010-02-03    -1.781314  winter     -0.058327     5.019723   
5   New York 2010-02-04    -6.886030  winter     -0.140805     5.113177   
6   New York 2010-02-05     7.386751  winter      0.131797     5.292168   
7   New York 2010-02-06    -5.574352  winter     -0.114384     5.382367   
8   New York 2010-02-07    -8.349027  winter     -0.251448     5.540993   
9   New York 2010-02-08     4.220088  winter     -0.112085     5.600809   
10  New York 2010-02-09     1.398394  winter     -0.078444     5.606951   
11  New York 2010-02-10    -3.087059  winter     -0.245900     5.619698   
12  New York 2010-02-11     2.801948  winter     -0.444305     5.391429   
13  New York 2010-02-12     0.771236  winter     -0.510485     5.362893   
14  New York 2010-02-13    -9.249576  winter     -0.766799     5.593583   
15  New York 2010-02-14    10.601015  winter     -0.156214     5.804578   
16  New York 2010-02-15    -0.230245  winter      0.003854     5.731226   
17  New York 2010-02-16     3.988327  winter      0.132921     5.777260   
18  New York 2010-02-17    -1.657875  winter      0.064441     5.786197   
19  New York 2010-02-18    -1.735687  winter      0.207177     5.682878   
20  New York 2010-02-19     4.636218  winter      0.539787     5.638726   
21  New York 2010-02-20     1.594853  winter      0.576603     5.641997   
22  New York 2010-02-21     3.375296  winter      0.743130     5.648635   
23  New York 2010-02-22    -6.968990  winter      0.634143     5.767595   
24  New York 2010-02-23   -10.752685  winter      0.512996     5.970645   
25  New York 2010-02-24     8.139836  winter      0.641582     6.094867   
26  New York 2010-02-25    -5.618275  winter      0.453367     6.200727   
27  New York 2010-02-26    -8.472446  winter     -0.189326     6.088640   
28  New York 2010-02-27    -2.564917  winter     -0.287031     6.102919   
29  New York 2010-02-28    -7.222193  winter     -0.872112     5.887518   

    temp_mean  temp_std   temp_min   temp_max  anomaly  
0    0.052858  4.998612 -15.692108  15.061622    False  
1    0.052858  4.998612 -15.692108  15.061622    False  
2    0.052858  4.998612 -15.692108  15.061622    False  
3    0.052858  4.998612 -15.692108  15.061622    False  
4    0.052858  4.998612 -15.692108  15.061622    False  
5    0.052858  4.998612 -15.692108  15.061622    False  
6    0.052858  4.998612 -15.692108  15.061622    False  
7    0.052858  4.998612 -15.692108  15.061622    False  
8    0.052858  4.998612 -15.692108  15.061622    False  
9    0.052858  4.998612 -15.692108  15.061622    False  
10   0.052858  4.998612 -15.692108  15.061622    False  
11   0.052858  4.998612 -15.692108  15.061622    False  
12   0.052858  4.998612 -15.692108  15.061622    False  
13   0.052858  4.998612 -15.692108  15.061622    False  
14   0.052858  4.998612 -15.692108  15.061622    False  
15   0.052858  4.998612 -15.692108  15.061622     True  
16   0.052858  4.998612 -15.692108  15.061622    False  
17   0.052858  4.998612 -15.692108  15.061622    False  
18   0.052858  4.998612 -15.692108  15.061622    False  
19   0.052858  4.998612 -15.692108  15.061622    False  
20   0.052858  4.998612 -15.692108  15.061622    False  
21   0.052858  4.998612 -15.692108  15.061622    False  
22   0.052858  4.998612 -15.692108  15.061622    False  
23   0.052858  4.998612 -15.692108  15.061622    False  
24   0.052858  4.998612 -15.692108  15.061622     True  
25   0.052858  4.998612 -15.692108  15.061622    False  
26   0.052858  4.998612 -15.692108  15.061622    False  
27   0.052858  4.998612 -15.692108  15.061622    False  
28   0.052858  4.998612 -15.6

In [14]:
# Построим график с выделением аномальных значений температуры, на этот раз для Берлина
fig = go.Figure()
fig.add_trace(go.Scatter(x=df[df['city']=='Berlin']['timestamp'], y=df[df['city']=='Berlin']['temperature'], 
                         name='temperature', line=dict(color='CornflowerBlue', width=1)))
fig.add_trace(go.Scatter(x=df[df['city']=='Berlin']['timestamp'], y=df[df['city']=='Berlin']['rolling_mean'], 
                         name='temperature rolling mean', line=dict(color='Navy', width=4)))
fig.add_trace(go.Scatter(x=df[(df['city']=='Berlin') & (df['anomaly']==True)]['timestamp'],
                         y=df[(df['city']=='Berlin') & (df['anomaly']==True)]['temperature'],
                         mode='markers', name='anomaly', line=dict(color='Purple', width=4)))
fig.update_layout(title='Temperature and rolling mean temperature in Berlin', 
                  xaxis=dict(title=dict(text='Date')),  yaxis=dict(title=dict(text='Temperature (degrees C)')))

In [15]:
# Кол-во аномалий по сезонам для каждого города
df[['city', 'season', 'anomaly']].groupby(['city', 'season']).sum()

anomaly
city           season         
Beijing        autumn       16
               spring       19
               summer       16
               winter       19
Berlin         autumn       17
               spring       16
               summer       18
               winter       34
Cairo          autumn       23
               spring       21
               summer       25
               winter       20
Dubai          autumn       16
               spring       24
               summer       22
               winter       21
London         autumn       19
               spring       22
               summer       25
               winter       25
Los Angeles    autumn       23
               spring       18
               summer       20
               winter       16
Mexico City    autumn       27
               spring       17
               summer       16
               winter       18
Moscow         autumn       19
               spring       21
               summer       19
               winter       21
Mumbai         autumn       21
               spring       23
               summer       22
               winter       21
New York       autumn       24
               spring       17
               summer       20
               winter       38
Paris          autumn       21
               spring       22
               summer       24
               winter       19
Rio de Janeiro autumn       23
               spring       21
               summer       23
               winter       22
Singapore      autumn       21
               spring       16
               summer       21
               winter       22
Sydney         autumn       19
               spring       23
               summer       18
               winter       23
Tokyo          autumn       27
               spring       24
               summer       21
               winter       23

In [16]:
# Температурные профили городов
city_profile = df[['city', 'temperature']].groupby(['city'], as_index=False)\
                    .agg(temp_mean=('temperature', 'mean'), temp_std=('temperature', 'std'), 
                         temp_min=('temperature', 'min'), temp_max=('temperature', 'max'))
city_profile

city  temp_mean   temp_std   temp_min   temp_max
0          Beijing  13.768003  11.403458 -16.545212  42.657388
1           Berlin  10.454250   8.519588 -15.486114  35.077247
2            Cairo  25.018633   8.571229  -3.774874  51.970598
3            Dubai  30.080364   8.567246   3.341856  55.060193
4           London  11.663772   6.838192 -11.701662  35.095612
5      Los Angeles  19.588809   6.191846   0.096748  43.365931
6      Mexico City  16.428239   5.891757  -4.307543  37.119959
7           Moscow   5.452504  11.163290 -26.042894  32.590492
8           Mumbai  29.978402   6.096257   9.863008  51.889113
9         New York  12.545155  10.200461 -15.692108  44.786657
10           Paris  12.217995   7.537665 -10.308451  39.627739
11  Rio de Janeiro  25.224427   6.174726   4.055122  45.295363
12       Singapore  27.408415   4.989656   8.482920  45.501343
13          Sydney  18.859236   6.730100  -5.988891  43.865638
14           Tokyo  16.654236   8.806083  -8.838914  46.477841

### Эксперименты с распараллеливанием функции

In [17]:
def get_temperature_data(city: str, data: pd.DataFrame) -> tuple[str, pd.DataFrame, float, pd.DataFrame, pd.DataFrame]:
    '''
        Функция принимает название города и датафрейм с данными температуры.
        Возвращает кортеж из отфильтрованного по городу датафрейма с добавленными столбцами скользящего среднего,
            стандартного отклонения, среднего, точек для линии тренда и индикатор аномальности значения температуры;
            число с плавающей точкой - коэффициент линии тренда, датафрейм с температурным профилем сезонов в выбранном
            городе и датафрейм с температурным профилем города.
    '''
    
    data = data[data['city'] == city]
    
    # Расчет скользящего среднего и скользящего std
    grouped_df = data.groupby(['city'])
    for city, group in grouped_df:
        data.loc[group.index, 'rolling_mean'] = group['temperature'].rolling(window=30).mean()
        data.loc[group.index, 'rolling_std'] = group['temperature'].rolling(window=30).std()
    
    data = data.dropna()
    
    # Получение линии тренда для одного города при помощи линейной регрессии
    X = data.dropna()[['timestamp']].astype('int')
    y = data.dropna()['rolling_mean']
    reg = LinearRegression()
    reg.fit(X, y)
    trend_line = X
    trend_line['trend_line_points'] = reg.predict(X)
    
    # Коэффициент линии тренда
    trend_line_coef = reg.coef_[0]
    
    # Температурные профили сезонов по городам
    seasons_profile = data[['city', 'season', 'temperature']].groupby(['city', 'season'], as_index=False)\
                        .agg(temp_mean=('temperature', 'mean'), temp_std=('temperature', 'std'), 
                            temp_min=('temperature', 'min'), temp_max=('temperature', 'max'))

    # Поиск аномальных значений температуры относительно средней температуры для сезона по городам
    data = pd.merge(data, seasons_profile, how='inner', on=['city', 'season'])
    data['anomaly'] = abs(data['temperature']) > abs(data['temp_mean']) + data['temp_std'] * 2
    
    # Температурные профили городов
    city_profile = data[['city', 'temperature']].groupby(['city'], as_index=False)\
                        .agg(temp_mean=('temperature', 'mean'), temp_std=('temperature', 'std'), 
                            temp_min=('temperature', 'min'), temp_max=('temperature', 'max'))
    
    return (city, data, trend_line_coef, seasons_profile, city_profile)

In [18]:
df = pd.read_csv('temperature_data.csv', parse_dates=['timestamp'])
cities = sorted(df['city'].unique())

In [19]:
%%time

# Замерим время синхронного выполнения функции для всех городов в цикле for

synch_processed_dfs = []

for city in cities:
    synch_processed_dfs.append(get_temperature_data(city, df))

CPU times: user 165 ms, sys: 3.08 ms, total: 168 ms
Wall time: 172 ms


In [20]:
%%time

# Замерим время параллельной работы на нескольких потоках

cities = df['city'].unique()
list_df = [chunk for chunk in df.groupby('city')]

parallel_threads_processed_dfs = Parallel(n_jobs=15, prefer="threads")(delayed(get_temperature_data)(*data) for data in list_df)

CPU times: user 156 ms, sys: 40.8 ms, total: 196 ms
Wall time: 177 ms


In [21]:
%%time
cities = df['city'].unique()
list_df = [chunk for chunk in df.groupby('city')]

parallel_processes_processed_dfs = Parallel(n_jobs=-1)(delayed(get_temperature_data)(*data) for data in list_df)

CPU times: user 70.7 ms, sys: 64 ms, total: 135 ms
Wall time: 2.58 s


Позапускал несколько раз, получилось, что распараллеливание на потоки в данном случае чаще работает немного дольше, иногда чуть быстрее ( в общем не дает стабильного преимущества в скорости выполнения). Распараллеливание на процессы работает существенно дольше (видимо в данном случае поднять процессы, а потом соединить результат их работы в один кортеж сильно дороже работы самой функции), но возможно на существенно большем объеме данных оно бы дало прирост.

### Работа с API OpenWeatherMap

In [22]:
API_KEY = '7ee8bac3cb89d52d712527d1a8c24772'

In [23]:
# Протестируем запросы к api на Москве
city = 'Moscow'
url = f'https://api.openweathermap.org/data/2.5/weather?q={city}&appid={API_KEY}&units=metric'

In [24]:
request = httpx.get(url)
request.status_code

200

In [25]:
# Значение текущей температуры
current_temp = request.json().get('main').get('temp')
current_temp

-2.96

In [26]:
city, data, trend_line_coef, seasons_profile, city_profile = get_temperature_data(city='Moscow', data=df)

mean_temp = seasons_profile.loc[seasons_profile['season']=='winter', 'temp_mean'].to_list()[0]
temp_std = seasons_profile.loc[seasons_profile['season']=='winter', 'temp_std'].to_list()[0]

if round(abs(mean_temp - current_temp) / temp_std, 2) > 2:
    print('Текущая температура является аномальной')
else:
    print('Текущая температура в пределах исторической нормы для сезона')    

Текущая температура в пределах исторической нормы для сезона


In [27]:
# Теперь посмотрим на текущую температуру во всех рассматриваемых городах

for city in cities:
    city_, data, trend_line_coef, seasons_profile, city_profile = get_temperature_data(city=city, data=df)
    mean_temp = seasons_profile.loc[seasons_profile['season']=='winter', 'temp_mean'].to_list()[0]
    temp_std = seasons_profile.loc[seasons_profile['season']=='winter', 'temp_std'].to_list()[0]
    
    url = f'https://api.openweathermap.org/data/2.5/weather?q={city}&appid={API_KEY}&units=metric'
    request = httpx.get(url)
    if request.status_code == 200:
        current_temp = request.json().get('main').get('temp')

        if round(abs(mean_temp - current_temp) / temp_std, 2) > 2:
            print(f'Текущая температура в городе {city} составляет {current_temp:.2f}С и является аномальной')
        else:
            print(f'Текущая температура в городе {city} составляет {current_temp:.2f}C и находится в пределах исторической нормы для сезона')
    
    else:
        print(f'Для города {city} код ответа: {request.status_code}')  

Текущая температура в городе New York составляет -6.54C и находится в пределах исторической нормы для сезона
Текущая температура в городе London составляет 6.49C и находится в пределах исторической нормы для сезона
Текущая температура в городе Paris составляет 5.21C и находится в пределах исторической нормы для сезона
Текущая температура в городе Tokyo составляет 3.83C и находится в пределах исторической нормы для сезона
Текущая температура в городе Moscow составляет -2.96C и находится в пределах исторической нормы для сезона
Текущая температура в городе Sydney составляет 21.73C и находится в пределах исторической нормы для сезона
Текущая температура в городе Berlin составляет 4.92C и находится в пределах исторической нормы для сезона
Текущая температура в городе Beijing составляет -7.06C и находится в пределах исторической нормы для сезона
Текущая температура в городе Rio de Janeiro составляет 26.29C и находится в пределах исторической нормы для сезона
Текущая температура в городе Dub

Проведем эксперимент, сравним время выполнения синхронной и асинхронной функции для получения текущей температуры.

In [28]:
# Синхронная функция для получения текущей температуры

def get_current_temperature(api_key: str, city: str) -> float | None:
    '''ОПИСАНИЕ'''
    
    url = f'https://api.openweathermap.org/data/2.5/weather?q={city}&appid={api_key}&units=metric'
    request = httpx.get(url)
    if request.status_code == 200:
        current_temp = request.json().get('main').get('temp')
        return current_temp
    else:
        print(f'Ошибка, сервер вернул ответ с кодом {request.status_code}')
        return None

In [29]:
# Измерим время работы синхронной функции получения текущей температуры на всех городах

start = time.time()

for city in cities:
    current_temp = get_current_temperature(API_KEY, city)
    if current_temp:
        print(f'Текущая температура в городе {city}: {current_temp}')

print(f'Время выполнения - {time.time() - start:.2f} секунд')

Текущая температура в городе New York: -6.54
Текущая температура в городе London: 6.49
Текущая температура в городе Paris: 5.21
Текущая температура в городе Tokyo: 3.83
Текущая температура в городе Moscow: -2.96
Текущая температура в городе Sydney: 21.73
Текущая температура в городе Berlin: 4.92
Текущая температура в городе Beijing: -7.06
Текущая температура в городе Rio de Janeiro: 26.29
Текущая температура в городе Dubai: 21.96
Текущая температура в городе Los Angeles: 15.2
Текущая температура в городе Singapore: 26.69
Текущая температура в городе Mumbai: 24.99
Текущая температура в городе Cairo: 17.42
Текущая температура в городе Mexico City: 17.75
Время выполнения - 3.62 секунд


In [30]:
# Асинхронная функция для получения текущей температуры

async def async_get_current_temperature(api_key: str, city: str) -> float | None:
    '''ОПИСАНИЕ'''

    url = f'https://api.openweathermap.org/data/2.5/weather?q={city}&appid={api_key}&units=metric'
    
    async with aiohttp.ClientSession() as session:
        async with session.get(url) as response:
            if response.status == 200:
                current_temp = await response.json() 
                return current_temp.get('main').get('temp')
            else:
                print(f'Ошибка, сервер вернул ответ с кодом {response.status}')
            return None

async def main(cities_list: list):
    '''
        Функция принимает ключ для OpenWeatherMap API и название города.
        Возвращает текущую температуру в выбранном городе.
    '''
    
    tasks = []
    for city in cities_list:
        tasks.append(asyncio.create_task(async_get_current_temperature(API_KEY, city)))
    return await asyncio.gather(*tasks)

In [31]:
# Измерим время работы асинхронной функции получения текущей температуры на всех городах

start = time.time()

temperatures_list = await main(cities)

for city, current_temp in zip(cities, temperatures_list):
    if current_temp:
        print(f'Текущая температура в городе {city}: {current_temp}') 

print(f'Время выполнения - {time.time() - start:.2f} секунд')

Текущая температура в городе New York: -6.54
Текущая температура в городе London: 6.49
Текущая температура в городе Paris: 5.21
Текущая температура в городе Tokyo: 3.83
Текущая температура в городе Moscow: -2.96
Текущая температура в городе Sydney: 21.73
Текущая температура в городе Berlin: 4.92
Текущая температура в городе Beijing: -7.06
Текущая температура в городе Rio de Janeiro: 26
Текущая температура в городе Dubai: 21.96
Текущая температура в городе Los Angeles: 15.2
Текущая температура в городе Singapore: 26.69
Текущая температура в городе Mumbai: 24.99
Текущая температура в городе Cairo: 17.42
Текущая температура в городе Mexico City: 17.75
Время выполнения - 0.20 секунд


В данном случае асинхронный подход дает значительный прирост в скорости (асинхронные запросы к api отрабатывают примерно в 15-20 раз быстрее)